<a href="https://colab.research.google.com/github/DilshadFayiz/AI-project-Biotecnika/blob/main/MOL_DOC_IKKB.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

(1) Install necessary Softwares and Libraries

In [ ]:
%pip install biopython rdkit py3Dmol

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 33.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.2/36.2 MB 45.0 MB/s eta 0:00:00


In [ ]:
# Install condacolab and restart the kernel
!pip install -q condacolab
import condacolab
condacolab.install()

⏬ Downloading https://github.com/jaimergp/miniforge/releases/download/24.11.2-1_colab/Miniforge3-colab-24.11.2-1_colab-Linux-x86_64.sh...
📦 Installing...
📌 Adjusting configuration...
🩹 Patching environment...
⏲ Done in 0:00:12
🔁 Restarting kernel...


In [ ]:
# Install py3Dmol using pip
!pip install -q py3Dmol

Traceback (most recent call last):
  File "/usr/local/bin/pip", line 7, in <module>
    from pip import main
ImportError: No module named pip


In [ ]:
# Install biopython using conda
!conda install -c conda-forge biopython -y

Channels:
 - conda-forge
Platform: linux-64
Solving environment: | / - done

## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - biopython


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    biopython-1.85             |  py311h49ec1c0_2         3.3 MB  conda-forge
    ca-certificates-2025.10.5  |       hbd8a1cb_0         152 KB  conda-forge
    certifi-2025.10.5          |     pyhd8ed1ab_0         156 KB  conda-forge
    conda-24.11.3              |  py311h38be061_0         1.1 MB  conda-forge
    libblas-3.9.0              |31_h59b9bed_openblas          16 KB  conda-forge
    libcblas-3.9.0             |31_he106b2a_openblas          16 KB  conda-forge
    libgfortran-14.2.0         |       h69a702a_2          52 KB  conda-forge
    libgfortran5-14.2.0        |       hf1ad2bd_2         1.4 MB  conda-forge
    liblapack-3.9.0            |31_h7ac8fdf_

In [ ]:
# Install rdkit using conda
!conda install -c conda-forge rdkit -y

Channels:
 - conda-forge
Platform: linux-64
Solving environment: | / - \ done


==> WARNING: A newer version of conda exists. <==
    current version: 24.11.3
    latest version: 25.9.1

Please update conda by running

    $ conda update -n base -c conda-forge conda



## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - rdkit


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    brotli-1.1.0               |       hb9d3cd8_2          19 KB  conda-forge
    brotli-bin-1.1.0           |       hb9d3cd8_2          18 KB  conda-forge
    cairo-1.18.4               |       h3394656_0         955 KB  conda-forge
    contourpy-1.3.3            |  py311hdf67eae_2         290 KB  conda-forge
    cycler-0.12.1              |     pyhd8ed1ab_1          13 KB  conda-forge
    cyrus-sasl-2.1.28          |       hd9c7081_0         205 KB  conda-forge
    font-ttf-de

In [ ]:
import os
from pathlib import Path
import py3Dmol
from Bio.PDB import PDBList
from rdkit import Chem
from rdkit.Chem import AllChem

**(2) Download Receptor**

## Nuclear factor kappa-B kinase subunit beta (IKKβ) PDB ID: **4KIK**

In [ ]:
pdbid = "4kik"
pdbl = PDBList()
pdbl.retrieve_pdb_file(pdbid, pdir='.', file_format='pdb')
if os.path.exists("pdb" + pdbid.lower() + ".ent"):
    os.rename("pdb" + pdbid.lower() + ".ent", pdbid + ".pdb")
    print("✅ PDB downloaded.")

✅ PDB downloaded.


**(3) Clean Protein and Save as PDB**

In [ ]:
singlepath = Path("/content/single-dock")
singlepath.mkdir(parents=True, exist_ok=True)
protein = "4kik.pdb"
with open(singlepath / "4kik_prot.pdb", "w") as g:
    with open(protein, 'r') as f:
        for line in f:
            if line.startswith("ATOM") or line.startswith("TER"):
                g.write(line)
        g.write("END\n")
print("✅ Cleaned receptor saved.")

✅ Cleaned receptor saved.


**(4) Prepare Receptor (MGLTools)**

In [ ]:
!conda install -c bioconda mgltools -y
!prepare_receptor4.py -r /content/single-dock/4kik_prot.pdb -o /content/single-dock/4kik_prot.pdbqt -A hydrogens -U nphs_lps

Channels:
 - bioconda
 - conda-forge
Platform: linux-64
Solving environment: - \ | / done


==> WARNING: A newer version of conda exists. <==
    current version: 24.11.3
    latest version: 25.9.1

Please update conda by running

    $ conda update -n base -c conda-forge conda



## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - mgltools


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    mgltools-1.5.7             |       h9ee0642_1       107.0 MB  bioconda
    ------------------------------------------------------------
                                           Total:       107.0 MB

The following NEW packages will be INSTALLED:

  mgltools           bioconda/linux-64::mgltools-1.5.7-h9ee0642_1 



                                                                        
Preparing transaction: - \ | / done
Verifying transaction: \ |

**(5)  Prepare Ligand (Using SMILES)**

In [ ]:
import pandas as pd

# Load the ligands from the CSV file
try:
    ligands_df = pd.read_csv("/content/MD_2.csv", encoding='latin-1') # Try latin-1 encoding
    print("Ligands loaded successfully!")
    display(ligands_df.head())
except FileNotFoundError:
    print("Error: ligands.csv not found. Please upload the file.")
except Exception as e:
    print(f"An error occurred while reading the CSV: {e}")

Ligands loaded successfully!


Compound                                             SMILES
0  BI-605906  CCC(F)(F)c1cc(N2CCC(S(C)(=O)=O)CC2)nc2sc(C(N)=...
1   TP-030-2  CN1C(=O)[C@@H](N2CCc3c(nn(Cc4ccccc4)c3Br)C2=O)...

**(6) Convert SMILES to 3D structures**

In [ ]:
from rdkit import Chem
from rdkit.Chem import AllChem

# Function to convert SMILES to 3D molecule
def smiles_to_3d_mol(smiles):
    try:
        # Convert SMILES to RDKit molecule object (2D)
        mol = Chem.MolFromSmiles(smiles)
        if mol is None:
            return None

        # Add hydrogens
        mol = Chem.AddHs(mol)

        # Generate 3D conformation
        # Use a try-except block to catch errors during 3D embedding
        try:
            AllChem.EmbedMolecule(mol, AllChem.ETKDGv2())
        except Exception as e:
            print(f"Error embedding molecule for {smiles}: {e}")
            return None


        # Optimize the 3D structure using the UFF force field
        # Use a try-except block to catch errors during optimization
        try:
            AllChem.UFFOptimizeMolecule(mol)
        except Exception as e:
            print(f"Error optimizing molecule for {smiles}: {e}")
            return None

        return mol
    except Exception as e:
        print(f"Error converting SMILES to 3D for {smiles}: {e}")
        return None

# Apply the function to the 'SMILES' column to create a new column with RDKit molecule objects
ligands_df['Mol_3D'] = ligands_df['SMILES'].apply(smiles_to_3d_mol)

# Display the DataFrame with the new 'Mol_3D' column (showing the first few rows)
display(ligands_df.head())

# Check how many molecules were successfully converted
successful_conversions = ligands_df['Mol_3D'].notna().sum()
print(f"\nSuccessfully converted {successful_conversions} out of {len(ligands_df)} ligands to 3D structures.")

Compound                                             SMILES  \
0  BI-605906  CCC(F)(F)c1cc(N2CCC(S(C)(=O)=O)CC2)nc2sc(C(N)=...   
1   TP-030-2  CN1C(=O)[C@@H](N2CCc3c(nn(Cc4ccccc4)c3Br)C2=O)...   

                                             Mol_3D  
0  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f6f0>  
1  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f920>


Successfully converted 2 out of 2 ligands to 3D structures.


**(7) Optimize ligand structures**

In [ ]:
from rdkit.Chem import AllChem

# Function to optimize molecule conformation
def optimize_mol_conformation(mol):
    if mol is None:
        return None
    try:
        # Use MMFF forcefield for optimization
        AllChem.MMFFOptimizeMolecule(mol)
        return mol
    except Exception as e:
        print(f"Error optimizing molecule: {e}")
        return None

# Apply the optimization function to the 'Mol_3D' column
ligands_df['Mol_3D_optimized'] = ligands_df['Mol_3D'].apply(optimize_mol_conformation)

# Display the DataFrame with the new 'Mol_3D_optimized' column
display(ligands_df.head())

# Check how many molecules were successfully optimized
successful_optimizations = ligands_df['Mol_3D_optimized'].notna().sum()
print(f"\nSuccessfully optimized {successful_optimizations} out of {len(ligands_df)} ligand structures.")

Compound                                             SMILES  \
0  BI-605906  CCC(F)(F)c1cc(N2CCC(S(C)(=O)=O)CC2)nc2sc(C(N)=...   
1   TP-030-2  CN1C(=O)[C@@H](N2CCc3c(nn(Cc4ccccc4)c3Br)C2=O)...   

                                             Mol_3D  \
0  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f6f0>   
1  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f920>   

                                   Mol_3D_optimized  
0  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f6f0>  
1  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f920>


Successfully optimized 2 out of 2 ligand structures.


**(8) Prepare ligands for AutoDock Vina**

In [ ]:
import os
from rdkit import Chem
from rdkit.Chem import AllChem
import subprocess # Import subprocess

# Create a directory to save the prepared ligands
output_dir = "/content/single-dock/ligands_pdbqt"
os.makedirs(output_dir, exist_ok=True)

# Function to convert RDKit molecule to PDBQT format
def mol_to_pdbqt(mol, ligand_name, output_dir):
    if mol is None:
        return None
    pdb_filename = f"{ligand_name}.pdb" # Use just the filename for the command
    pdbqt_filename_mgl = f"{ligand_name}_mgl.pdbqt" # Use just the filename for the command
    full_pdb_path = os.path.join(output_dir, pdb_filename)
    full_pdbqt_path = os.path.join(output_dir, pdbqt_filename_mgl)


    try:
        # Write as PDB first
        Chem.MolToPDBFile(mol, full_pdb_path)

        # Verify the PDB file exists before proceeding
        if not os.path.exists(full_pdb_path):
            print(f"Error: PDB file was not created for {ligand_name}: {full_pdb_path}")
            return None

        # Use prepare_ligand4.py from MGLTools to convert PDB to PDBQT
        # Use subprocess to capture output and errors
        # Change directory to output_dir before running the command
        original_dir = os.getcwd()
        os.chdir(output_dir)

        prepare_lig_command = ["python2", "/usr/local/bin/prepare_ligand4.py", "-l", pdb_filename, "-o", pdbqt_filename_mgl, "-A", "hydrogens", "-U", "nphs_lps", "-v"]


        process = subprocess.Popen(prepare_lig_command, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        stdout, stderr = process.communicate()

        # Change back to the original directory
        os.chdir(original_dir)


        if process.returncode != 0:
            print(f"Error running prepare_ligand4.py for {ligand_name}:")
            print(f"Stdout: {stdout.decode()}")
            print(f"Stderr: {stderr.decode()}")
            # Clean up the intermediate .pdb file even if conversion failed
            if os.path.exists(full_pdb_path):
                os.remove(full_pdb_path)
            return None

        # Clean up the intermediate .pdb file
        if os.path.exists(full_pdb_path):
            os.remove(full_pdb_path)

        # Check if the PDBQT file was actually created
        if os.path.exists(full_pdbqt_path):
            return full_pdbqt_path
        else:
            print(f"prepare_ligand4.py finished without error but did not create {full_pdbqt_path}")
            return None


    except Exception as e:
        print(f"Error converting molecule {ligand_name} to PDBQT: {e}")
        # Ensure intermediate PDB is removed in case of other exceptions
        if os.path.exists(full_pdb_path):
            os.remove(full_pdb_path)
        # Ensure we are back in the original directory in case of exception before os.chdir(original_dir)
        if os.getcwd() != original_dir:
            os.chdir(original_dir)
        return None

# Apply the conversion function to the DataFrame
# Ensure 'Mol_3D_optimized' column exists and contains RDKit mol objects
if 'Mol_3D_optimized' in ligands_df.columns:
    # Based on the previous output, the column with compound names is 'BDBM16789'
    compound_name_column = 'Compound' # Corrected column name
    ligands_df['PDBQT_Filename'] = ligands_df.apply(
        lambda row: mol_to_pdbqt(row['Mol_3D_optimized'], row[compound_name_column], output_dir), axis=1
    )
    print("\nLigands prepared and saved as .pdbqt files.")
else:
    print("\nError: 'Mol_3D_optimized' column not found. Please ensure the optimization step was successful.")


# Display the DataFrame with the new 'PDBQT_Filename' column
display(ligands_df.head())

# Check how many ligands were successfully converted to PDBQT
successful_pdbqt_conversions = ligands_df['PDBQT_Filename'].notna().sum()
print(f"\nSuccessfully prepared {successful_pdbqt_conversions} out of {len(ligands_df)} ligands in PDBQT format.")

# List the generated PDBQT files
print(f"\nGenerated PDBQT files in: {output_dir}")
!ls {output_dir} | head -n 10 # Display the first 10 generated files


Ligands prepared and saved as .pdbqt files.


Compound                                             SMILES  \
0  BI-605906  CCC(F)(F)c1cc(N2CCC(S(C)(=O)=O)CC2)nc2sc(C(N)=...   
1   TP-030-2  CN1C(=O)[C@@H](N2CCc3c(nn(Cc4ccccc4)c3Br)C2=O)...   

                                             Mol_3D  \
0  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f6f0>   
1  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f920>   

                                   Mol_3D_optimized  \
0  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f6f0>   
1  <rdkit.Chem.rdchem.Mol object at 0x7f84b186f920>   

                                      PDBQT_Filename  
0  /content/single-dock/ligands_pdbqt/BI-605906_m...  
1  /content/single-dock/ligands_pdbqt/TP-030-2_mg...


Successfully prepared 2 out of 2 ligands in PDBQT format.

Generated PDBQT files in: /content/single-dock/ligands_pdbqt
BI-605906_mgl.pdbqt
TP-030-2_mgl.pdbqt


**(9) Define the Docking Box**

In [ ]:
# Define the center coordinates of the docking box (IKKβ)
center_x = 18.12
center_y = -12.4435
center_z = -49.4985

# Define the dimensions of the docking box
# These are example values, you should replace them with the actual dimensions for your binding site
size_x = 129.178
size_y = 136.281
size_z = 100.997
print(f"Docking box center: ({center_x}, {center_y}, {center_z})")
print(f"Docking box size: ({size_x}, {size_y}, {size_z})")

Docking box center: (18.12, -12.4435, -49.4985)
Docking box size: (129.178, 136.281, 100.997)


**(10) Before running AutoDock Vina, we need to download the executable**

In [ ]:
# Download AutoDock Vina
!wget -q https://github.com/ccsb-scripps/AutoDock-Vina/releases/download/v1.2.5/vina_1.2.5_linux_x86_64

# Make the executable runnable
!chmod +x vina_1.2.5_linux_x86_64

**(11)  Run AutoDock Vina**

In [ ]:
import os
import subprocess

# Define the path to the receptor PDBQT file
receptor_pdbqt = "/content/single-dock/4kik_prot.pdbqt"

# Define the directory containing the prepared ligand PDBQT files
ligands_pdbqt_dir = "/content/single-dock/ligands_pdbqt"

# Define the output directory for docking results
output_dir = "/content/single-dock/docking_results"
os.makedirs(output_dir, exist_ok=True)

# Get a list of all ligand PDBQT files
ligand_files = [f for f in os.listdir(ligands_pdbqt_dir) if f.endswith(".pdbqt")]

print(f"Starting docking for {len(ligand_files)} ligands...")

# Define the full path to the vina executable
# The path has been corrected to reflect the download location
vina_executable = "/content/vina_1.2.5_linux_x86_64"

# Iterate through each ligand file and run Vina
for ligand_file in ligand_files:
    ligand_path = os.path.join(ligands_pdbqt_dir, ligand_file)
    # Define the output file name for the docking results for this ligand
    output_file = os.path.join(output_dir, f"{os.path.splitext(ligand_file)[0]}_vina_out.pdbqt")

    # Construct the Vina command using the full executable path
    vina_command = [
        vina_executable, # Use the full path here
        "--receptor", receptor_pdbqt,
        "--ligand", ligand_path,
        "--center_x", str(center_x),
        "--center_y", str(center_y),
        "--center_z", str(center_z),
        "--size_x", str(size_x),
        "--size_y", str(size_y),
        "--size_z", str(size_z),
        "--out", output_file,
        # Removed --log option as it's not supported in this Vina version
        # You can add other Vina parameters here, like --num_modes, --energy_range, --exhaustiveness, etc.
        # "--num_modes", "10",
        # "--energy_range", "3",
        # "--exhaustiveness", "8"
    ]

    print(f"Running Vina for {ligand_file}...")
    try:
        # Run the Vina command
        process = subprocess.Popen(vina_command, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        stdout, stderr = process.communicate()

        if process.returncode != 0:
            print(f"Error running Vina for {ligand_file}:")
            print(f"Stdout: {stdout.decode()}")
            print(f"Stderr: {stderr.decode()}")
        else:
            print(f"Successfully docked {ligand_file}. Results saved to {output_file}")

    except FileNotFoundError:
        print("Error: Vina executable not found at the specified path. Make sure the path is correct.")
        break # Stop the loop if Vina executable is not found
    except Exception as e:
        print(f"An error occurred while running Vina for {ligand_file}: {e}")


print("\nDocking simulation finished.")

# You can then analyze the docking results in the 'docking_results' directory.
# The docking results (binding energies and poses) will be in the .pdbqt output files.
# You can parse these files to extract the binding energies.

Starting docking for 2 ligands...
Running Vina for BI-605906_mgl.pdbqt...
Successfully docked BI-605906_mgl.pdbqt. Results saved to /content/single-dock/docking_results/BI-605906_mgl_vina_out.pdbqt
Running Vina for TP-030-2_mgl.pdbqt...
Successfully docked TP-030-2_mgl.pdbqt. Results saved to /content/single-dock/docking_results/TP-030-2_mgl_vina_out.pdbqt

Docking simulation finished.


**(12) Extract Binding Energies from Vina Output**

In [ ]:
import os
import pandas as pd

# Define the directory containing the docking results
docking_results_dir = "/content/single-dock/docking_results"

# Initialize a list to store the docking results
docking_results = []

# Iterate through each output PDBQT file
for result_file in os.listdir(docking_results_dir):
    if result_file.endswith("_vina_out.pdbqt"):
        ligand_name = result_file.replace("_mgl_vina_out.pdbqt", "") # Extract ligand name

        # Construct the full path to the result file
        result_path = os.path.join(docking_results_dir, result_file)

        try:
            with open(result_path, 'r') as f:
                binding_energy = None
                # Read the file line by line to find the binding energy
                for line in f:
                    if line.startswith("REMARK VINA RESULT:"):
                        # Extract the binding energy (the second value in the line)
                        parts = line.split()
                        if len(parts) > 3:
                            try:
                                binding_energy = float(parts[3])
                                break # Assuming the first REMARK VINA RESULT line is the best pose
                            except ValueError:
                                print(f"Could not parse binding energy from line in {result_file}: {line}")
                                continue
                if binding_energy is not None:
                    docking_results.append({'Compound_Name': ligand_name, 'Binding_Energy': binding_energy})
                else:
                    print(f"Binding energy not found in {result_file}")

        except FileNotFoundError:
            print(f"Error: Result file not found: {result_path}")
        except Exception as e:
            print(f"An error occurred while processing {result_file}: {e}")

# Create a pandas DataFrame from the results
docking_results_df = pd.DataFrame(docking_results)

# Sort the DataFrame by binding energy (lower energy is better)
docking_results_df = docking_results_df.sort_values(by='Binding_Energy')

# Display the results
print("\nDocking Results (Sorted by Binding Energy):")
display(docking_results_df)


Docking Results (Sorted by Binding Energy):


Compound_Name  Binding_Energy
0      TP-030-2         -10.074
1     BI-605906          -9.052

In [ ]:
# Save the docking results to a CSV file
output_csv_path = "/content/single-dock/binding_energies(2).csv"
docking_results_df.to_csv(output_csv_path, index=False)

print(f"\nBinding energies saved to: {output_csv_path}")


Binding energies saved to: /content/single-dock/binding_energies(2).csv


**(13)  Visualize Docked Poses**

In [ ]:
import py3Dmol
import os

# Define the paths to the receptor and docking results
receptor_pdbqt = "/content/single-dock/4kik_prot.pdbqt"
docking_results_dir = "/content/single-dock/docking_results"

# Get a list of all docked ligand PDBQT files
docked_ligand_files = [f for f in os.listdir(docking_results_dir) if f.endswith("_vina_out.pdbqt")]

if not docked_ligand_files:
    print("No docked ligand PDBQT files found in the results directory.")
else:
    print(f"Visualizing docked poses for {len(docked_ligand_files)} ligands...")

    # Iterate through each docked ligand file and visualize the pose
    for ligand_file in docked_ligand_files:
        ligand_name = ligand_file.replace("_mgl_vina_out.pdbqt", "") # Extract ligand name
        ligand_pdbqt_path = os.path.join(docking_results_dir, ligand_file)

        if os.path.exists(ligand_pdbqt_path):
            print(f"\nVisualizing docked pose for: {ligand_name}")

            # Create a new view for each ligand
            view = py3Dmol.view(width=800, height=600)

            # Add receptor
            try:
                with open(receptor_pdbqt, 'r') as f:
                    receptor_data = f.read()
                view.addModel(receptor_data, 'pdbqt')
                print(f"Receptor model added.")
            except Exception as e:
                print(f"Error loading or adding receptor model: {e}")
                continue # Skip to the next ligand if receptor fails to load

            # Add ligand (first pose)
            try:
                with open(ligand_pdbqt_path, 'r') as f:
                    ligand_data = f.read()
                if not ligand_data:
                    print(f"Warning: Ligand file {ligand_file} is empty.")
                    continue # Skip this ligand if the file is empty

                view.addModel(ligand_data, 'pdbqt')
                print(f"Ligand model added.")
            except Exception as e:
                print(f"Error loading or adding ligand model {ligand_file}: {e}")
                continue # Skip to the next ligand if ligand fails to load


            # Style the receptor (Model 0)
            view.setStyle({'model': 0}, {'cartoon': {'color': 'spectrum'}})

            # Style the ligand (Model 1) - Directly attempt to style model 1
            try:
                view.setStyle({'model': 1}, {'stick': {}})
                print(f"Ligand model styled.")
            except Exception as e:
                 print(f"Warning: Could not style ligand model (model 1) for {ligand_file}: {e}")


            # Zoom to the receptor
            view.zoomTo({'model': 0})

            # Render the view
            view.show()

        else:
            print(f"Error: Docking output file not found for {ligand_name}: {ligand_pdbqt_path}")

    print("\nFinished visualizing all docked poses.")

Visualizing docked poses for 2 ligands...

Visualizing docked pose for: TP-030-2
Receptor model added.
Ligand model added.
Ligand model styled.


3Dmol.js failed to load for some reason. Please check your browser console for error messages.


Visualizing docked pose for: BI-605906
Receptor model added.
Ligand model added.
Ligand model styled.


3Dmol.js failed to load for some reason. Please check your browser console for error messages.


Finished visualizing all docked poses.
